<center>
    <h1>Modeling an Electron in a Field of Secured Point Charges</h1>
</center>

<h2>Introduction</h2>

Kinetics typically makes sense. You can see kinetics. But, you can't really see an electric field. The idea that an electron will move towards a positive charge and away from a negative charge might make sense, but it can be difficult to visualize where an electron might go in a more complicated field of charges. This project is about helping students in physics classes understand how electrons are moved in electric fields

In my project, we are looking at an idealized simulation. The only forces present on the electron are the forces created by the charges, and those charges are all point charges fixed in place that won't be affected by each other. While not an extrememly realistic situation, it is a good situation for beginners to get a better understanding.

The simulation relies on Coulomb's Law, which is used to calculate the force on a point charge by another point charge. It also uses Newton's Second Law (f=ma) to get acceleration from force. Finally, we use Reimann sums, as velocity is the area under the curve of acceleration and position the area under the curve of velocity.

<h2>Methodology</h2>

<h3>Imports and Libraries</h3>

<p>When creating something, what's the first thing you do? Most likely it is a brainstorm or sketch, but after that you need to gather the tools you need to make it. Whether that's information or supplies, you most likely don't have everything you need immediately. Coding is similar, especially in Python. There are plenty of resources you can find on the internet that can help you learn what you need, and there's also many libraries of code open to the public that have snippets of code available to be imported right into your project.</p>
<p>Importing code from Python libraries is similiar to borrowing books. If you know exactly what you need, you can import specific functions (ways of doing things) and constants (values) from a library. If you just need a specific subsection, you can import that subsection, like borrowing a bunch of books by one author. And if you need access to a whole library, well, that's fine to because with coding libraries there's infinite copies of every book.</p>
<p>For my project, while I borrowed a couple of things immediately, such as <em>matplotlib.pyplot</em> because I knew I would need it for graphing, many of the other things I added to this section as I learned I needed them, such as <em>HTML</em> from <em>IPython.display</em>, which I needed to make the model visible for users.</p>
<p>Each of these imports are used for various reasons, and they form the base of my code. I'll be explaining each of them in more detail when they pop up again later.</p>

In [2]:
import math #basic python math library, used for square rooting and getting pi
#https://docs.python.org/3/library/math.html#
import numpy as np #common library, source of numpy arrays which are easier to manipulate as vectors than your average python list
#https://numpy.org/doc/stable/index.html

from scipy.constants import e, m_e, epsilon_0 
#physics constants I need, the charge of a proton or electron (e), the mass of an electron (m_e), and epsilon naught
#https://docs.scipy.org/doc/scipy/reference/constants.html

import matplotlib.pyplot as plt #for plotting data
#https://matplotlib.org/3.5.3/api/_as_gen/matplotlib.pyplot.html
import matplotlib.animation as animation #to create animation
#https://matplotlib.org/stable/api/animation_api.html
from IPython.display import HTML #making it possible to display my animation
#https://ipython.readthedocs.io/en/stable/api/generated/IPython.display.html

<h3>Basic Objects (Charge)</h3>

<p>One of the major elements of the model are charges. Since the point of this model is to allow users to explore what happens to electrons in field of point charges, the first thing I did was create a way to represent charges, as their much more simple than an electron, as they are being held still.</p>
<p>Charges have two parts, a position and a charge. This Object, named Charge, is a way to hold both of those values under a single name, making it easy to figure out which charge has which position and charge when there are multiple charges.</p>
<p>There's two many parts to this Object. The first part is creating it, which is giving the values for the object to hold. For the position, it is held in a ndarray, which acts as a vector, allowing for positions to be added and subtracted, which is useful when the distance between a charge and an electron needs to be found (<em>The N-dimensional</em>, n.d.). For the charge, it is simply a number that equals the value of the charge.</p>
<p>The second part is two methods, which make it so in other parts of the program I can access the position and charge of a charge. All they do is give back the value asked for.</p>

In [3]:
class Charge: #class to create Charge objects, which will make it easier to work with charges

    def __init__(self, x, y, charge): #initiation function, magic method
        self.position = np.array([float(x), float(y)]) ##creating the position, using the given x and y coordinates, as an array
        #https://numpy.org/doc/stable/reference/generated/numpy.array.html
        self.charge = charge #getting the charge of the particle

    def get_position(self): #function to get the position of a charge
        return self.position #return the position

    def get_charge(self): #function to get the charge of a charge
        return self.charge #return the charge

<h3>Complicated Objects (Electron)</h3>

<p>The other major element of the model is the electron, which is much more complicated than the charges because the electron has to move. Beyond jsut holding values like a Charge Object, the Electron Object also needs to be able to do calculations to determine where the electron should be as its position changes during each frame of the animation.</p>
<p>An electron has a position, which is held in an ndarray like with the position of a charge. The velocity and acceleration of an electron are vectors, so they are also held in an ndarray. Every electron has a charge of -e, so the charge of an electron is automatically set to -e.</p>
<p>Additionally, there are methods to get the position, velocity, and acceleration, as all three are needed later on in other parts of the program for various purposes. Since all electrons can be assumed to have a charge of -e, there is no need for there to be a method to get an electron's charge.</p>
<p>Next there are the methods that make it possible for the force to be calculated. The force on an object can be calculated by adding up all of the forces affecting the object, and in this model the only forces that matter are the forces that the charges place on an electron. The force between two points charges can be found with Couloumb's Law:</p>
$$
    F=\frac{q_1*q_2}{4\pi*e_0}*\frac{r_1-r_2}{|r_1-r_2|^3}
$$
<p>By finding the force for each charge, all of them can be added up to get the total force. From the force, acceleration can be found using Newton's Second Law ($f=ma$). For the purposes of the model, I slightly adjust the acceleration by dividing by an additional 100 so the acceleration is smaller than found. This is because using the actual acceleration results in the model failing due to consistent overshooting of position. Since force is inversely proportional to the square of the distance between the electron and a charge, once the electron gets too far away it will never course correct back to where it should end up. As large movements make it easy for the model to mess up, I've added in the adjustment to increase accuracy.</p>
<p>Then for finding velocity and position, I used the fact that velocity is the area under the curve of acceleration and position the area under the curve of velocity. Using this knowledge, I can find the approximate value of velocity and position using Reimann Sums. By saying the time between each frame is 0.1 second, I can multiply the current acceleration by 0.1 and add it to the velocity to find the current velocity. This same process works for position.</p>

In [4]:
class Electron: #class to create Electron objects, which will allow me to make functions for electrons

    def __init__(self, x, y): #initiation function, magic method
        self.position = np.array([float(x), float(y)]) #creating the position, using the given x and y coordinates, as an array
        self.charge = -e #all electrons have a charge of -e
        self.velocity = np.array([0.0, 0.0]) #start with 0 velocity
        self.acceleration = np.array([0.0, 0.0]) #start with 0 acceleration

    def get_position(self): #function to get the position of an electron
        return self.position #return the position

    def get_velocity(self): #function to get the velocity of an electron
        return self.velocity #return the velocity
    
    def get_acceleration(self): #function to get the acceleration of an electron
        return self.acceleration #return acceleration

    def get_force(self, charges): #function to get the sum of all the forces on an electron
        force = np.array([0.0, 0.0]) #start with 0
        for charge in charges: #then go through each charge
            r = math.sqrt((charge.get_position() - self.get_position())[0] ** 2 + (charge.get_position() - self.get_position())[1] ** 2)
            #get the distance from electron to charge
            force += (self.get_position() - charge.get_position()) * charge.get_charge() * self.charge / 4 / math.pi / epsilon_0 / (r ** 3)
            #use Coulomb's Law to find the force a single charge places on the electron and add it to the current force
        self.acceleration = force / m_e / 100 #Newton's second law, f=ma, so a=f/m

    def update_velocity(self): #changing velocity
        self.velocity += self.acceleration * .1 #small increments, velocity changes by acceleration

    def update_position(self): #changing position
        self.position += self.velocity * .1 #small increments, position changes by velocity

<h3>Repeated Function</h3>

<p>When coding, if there's something you want to do multiple times, you make a function so you just need to use one line instead of copying and pasting a bunch of lines over and over again. Every frame, I knew I'd need to update the electron, so I decided to make a function to do just that. While I actually only ended up needing to use this function once, I decided to keep it to make my code more readable.</p>
<p>What this does is exactly what it says, it updates everything about the electron. The first thing it does is find the force, and through that, the acceleration. Then, it goes in order, updating velocity then position. This process is what would always happen when the electron moves, so it is nice to have a function to clearly show how the process works and in what order.</p>

In [5]:
def electron_update(charges, electron): #function to update the state of the electron

    electron.get_force(charges) #getting the current force
    electron.update_velocity() #updating velocity
    electron.update_position() #updating position

<h3>Generator Function</h3>

<p>When creating my model, I needed to find a way to stop it. It's simple to just have an animation be built for a specific number of frames, but for this model I needed to have it stop generating frames when specific conditions were reached, and a generator function was the solution to that problem. With generator functions, the animation will continue as long as a number is given back instead of nothing (ImportanceOfBeingErnest, 2018). There are three conditions where the animation should stop and the model should be done being created.</p>
<p>The first is if the elecetron is touching a charge, which should only happen with a positive charge. Since the distance between charges will be so small at that point, the force of that one charge will overwhelm every other force and the electron will stay on that charge. My code can't understand that though, and would slingshot my electron out if I didn't stop the model. So, if the electron tooks a charge, the animation will stop. There's some range allowed because it's highly unlikely that the electron will ever have the exact same position as a charge.</p>
<p>The next condition is if the electron leaves the boundaries of my graph. I've made the assumption that since force is inversely proportional to distance squared, once an electron leaves the boundaries of my graph it is never coming back because acceleration will never (or at least, never in a reasonable amount of time) be able to turn the velocity back around.</p>
<p>Lastly, if both acceleration and velocity are [0, 0], the electron will not move again. Under those circumstances, it makes the most sense to stop modeling, as nothing will change from that point.</p>
<p>If none of these conditions are met, that means the model is not complete and another frame should be generated, so I give back a number so that the program knows the animation is not done being created.</p>

In [6]:
def gen(charges, electron): #making a generator function!
    i = 1 #start with one frame
    sep = True #boolean to determine if you should continue
    while sep:
        #print(i)
        for charge in charges: #look at each charge
            if abs(electron.get_position()[0] - charge.get_position()[0]) < 2 and abs(electron.get_position()[1] - charge.get_position()[1]) < 2:
            #if the electron is practically on the charge
                sep = False #don't continue
                print("on charge") #let us know we are on a charge
                print(charge.get_position(), electron.get_position()) #print both locations
                print(abs(electron.get_position()[0] - charge.get_position()[0]), abs(electron.get_position()[1] - charge.get_position()[1])) #print distance
                break #exit this loop
        if abs(electron.get_position()[0]) > 100 or abs(electron.get_position()[1]) > 100: #if it's outside of the boundaries of the simulation
            print("left boundaries")
            sep = False #don't continue
        if np.array_equal(electron.get_velocity(), [0.0,0.0]) and np.array_equal(electron.get_acceleration(), [0.0, 0.0]): #if the velocity + acceleration is 0
            print("no velocity/acceleration") #let us know that the velocity/acceleration is 0
            print(electron.get_velocity(), electron.get_acceleration()) #prove it
            sep = False #don't continue
        if sep == True: #if we still should continue
            i += 1 #up the frame number
            #print(i)
            yield i #iteration version of return

<h3>Modeling</h3>

<p>In order to keep everything organized, I made a function to create the model, even though that only happens once. In order to create this model, the list of charges and the electron are included because those are all needed to create the model.</p>
<p>First is setting up the graph and the first frame for the model. For this, all of the charges are added to a scatter plot, with positive charges colored red and negative charges colored blue. The electron is placed in its first position and colored green. The dimensions of the scatter plot are set to -100, 100 in the x and y direction. Finally, the legend is made visible so that users know what the different colors mean.</p>
<p>Next is writing a function that can be used for updating the frames of the animation used to create the model. The new position for the electron is calculated with <em>electron_update(charges, electron)</em>, the electron point in the scatter plot is moved to this new position, and the scatter plot for this next frame is given back.</p>
<p>After that, the actual animation is created. Before anything happens, an initial force is calculated so that the program doesn't immediately assume acceleration and velocity are both [0,0]. Then, an animation is made. This animation takes the figure where the scatter plots exist, the function used to update the frames, the number of frames (this is where the generator function comes in), how much time there should be inbetween frames (10 milliseconds), and a backup frame count.</p>
<p>Finally, the animation is returned after being transformed into a form where users can see all parts of the animation, instead of just a singular frame.</p>

In [7]:
def create_animation(charges, electron): #creating the animation

    fig, ax = plt.subplots() #needed elements of the plot
    #https://matplotlib.org/stable/api/_as_gen/matplotlib.pyplot.subplots.html
    
    scatter = ax.scatter([c.get_position()[0] for c in charges if c.get_charge() > 0], [c.get_position()[1] for c in charges if c.get_charge() > 0], c="r", label="+ charges")
    #placing all of the positive charges on the plot, coloring them red
    #https://matplotlib.org/stable/api/_as_gen/matplotlib.axes.Axes.scatter.html#matplotlib.axes.Axes.scatter
    scatter = ax.scatter([c.get_position()[0] for c in charges if c.get_charge() < 0], [c.get_position()[1] for c in charges if c.get_charge() < 0 ], c="b", label="- charges")
    #placing all of the negative charges on the plot, coloring them blue
    scatter = ax.scatter(electron.get_position()[0], electron.get_position()[1], c="g", label="electron")
    #place the electron on the plot, coloring it green

    ax.set_xlim([-100, 100]) #making the x-axis -100 to 100
    #https://matplotlib.org/stable/api/_as_gen/matplotlib.axes.Axes.set_xlim.html
    ax.set_ylim([-100, 100]) #making the y-axis -100 to 100
    #https://matplotlib.org/stable/api/_as_gen/matplotlib.axes.Axes.set_ylim.html
    ax.legend() #show the legend
    #https://matplotlib.org/stable/api/_as_gen/matplotlib.axes.Axes.legend.html
    
    def update(frame): #update function!

        electron_update(charges, electron) #call the update function to set the values
        scatter.set_offsets(electron.get_position()) #update the position of the electron
        #https://matplotlib.org/stable/api/collections_api.html#matplotlib.collections.AsteriskPolygonCollection.set_offsets
        return scatter #return the new scatter plot

    electron.get_force(charges) #not have starting acceleration 0
    anim = animation.FuncAnimation(fig=fig, func=update, frames=gen(charges, electron), interval=10, save_count=1000) #create the animation
    #https://matplotlib.org/stable/api/_as_gen/matplotlib.animation.FuncAnimation.html
    plt.close() #close the plot

    return HTML(anim.to_jshtml()) #return the HTML to make the animation
    #https://matplotlib.org/stable/api/_as_gen/matplotlib.animation.Animation.html#matplotlib.animation.Animation.to_jshtml

<h3>The Program</h3>

<p>Really, when it comes down to it, everything before this was set up. While that was all need to make the model, this is where everything is actually happening and where users get to decide what is in their model.</p>
<p>I start by explaining what this program will do and what the limitations of the graph is through print statements, which make code visible to users.</p>
<p>Then, charges are created. I ask users how many charges they want in their model, and then I take that number and ask a user what the details of the charge is for as many charges as they decide. Users give x and y coordinates, and the charge, which I multiply by e in order to put the charges at a similiar value to a group of protons or electrons.</p>
<p>Next, the electron is created by asking users where the electron should go, getting the x and y coordinates.</p>
<p>Finally, I call the function to create the animation, and after a bit of waiting, users will be able to see the model for the situation they gave.</p>

In [8]:
print("This program will create a 2d simulation with point charges fixed in place and an unsecured electron.")
print("The dimensions are (-100, 100) by (-100, 100).")
print()

print("First, create your Charges.")
q = int(input("Number of Charges (int): "))
charges = []
for i in range(q):
    x = float(input("Enter x coordinate (float): "))
    y = float(input("Enter y coordinate (float): "))
    c = float(input("Enter charge (float): "))
    charges.append(Charge(x, y, c * e))
    
print("Second, locate your Electron.")
x = float(input("Enter x coordinate (float): "))
y = float(input("Enter y coordinate (float): "))
electron = Electron(x, y)

create_animation(charges, electron)

This program will create a 2d simulation with point charges fixed in place and an unsecured electron.
The dimensions are (-100, 100) by (-100, 100).

First, create your Charges.


Number of Charges (int):  7
Enter x coordinate (float):  1
Enter y coordinate (float):  2
Enter charge (float):  3.5
Enter x coordinate (float):  -7
Enter y coordinate (float):  -10
Enter charge (float):  8.9
Enter x coordinate (float):  17
Enter y coordinate (float):  -30
Enter charge (float):  12
Enter x coordinate (float):  90
Enter y coordinate (float):  86
Enter charge (float):  -5
Enter x coordinate (float):  78
Enter y coordinate (float):  45
Enter charge (float):  6
Enter x coordinate (float):  46
Enter y coordinate (float):  85
Enter charge (float):  3.9
Enter x coordinate (float):  34
Enter y coordinate (float):  32
Enter charge (float):  -40


Second, locate your Electron.


Enter x coordinate (float):  10
Enter y coordinate (float):  20


on charge
[ -7. -10.] [-8.31864225 -8.24720509]
1.3186422507313047 1.752794914977784


<h2>Results and Discussion</h2>

<h2>Conclusion</h2>

<h2>Citations</h2>

<p>
    ImportanceOfBeingErnest. (2018, February 1). <em>How to stop FuncAnimation by func
     in matplotlib? </em>[Online forum post]. Stack Overflow.
     https://stackoverflow.com/questions/48564181/
     how-to-stop-funcanimation-by-func-in-matplotlib
</p>
<p>
    <em>The n-dimensional array (ndarray)</em>. (n.d.). NumPy. Retrieved May 9, 2024, from
     https://numpy.org/doc/stable/reference/arrays.ndarray.html
</p>